In [1]:
import tensorflow as tf
print(tf.__version__)

2.5.0


In [2]:
from tensorflow.keras.preprocessing.text import Tokenizer #Tokenize words to numerical format
from tensorflow.keras.preprocessing.sequence import pad_sequences #Every word must have same length for matrix representation
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense,Flatten,Embedding,Activation, Dropout
from tensorflow.keras.layers import Conv1D, MaxPooling1D, GlobalMaxPooling1D

In [3]:
import numpy as np
import pandas as pd
from numpy import array
from sklearn.model_selection import train_test_split

# Exploratory Data Analysis

In [4]:
data = pd.read_csv("/content/drive/My Drive/fake.csv")
data.shape

(12999, 20)

In [5]:
data.head(5)

uuid  ord_in_thread  ... shares  type
0  6a175f46bcd24d39b3e962ad0f29936721db70db              0  ...      0  bias
1  2bdc29d12605ef9cf3f09f9875040a7113be5d5b              0  ...      0  bias
2  c70e149fdd53de5e61c29281100b9de0ed268bc3              0  ...      0  bias
3  7cf7c15731ac2a116dd7f629bd57ea468ed70284              0  ...      0  bias
4  0206b54719c7e241ffe0ad4315b808290dbe6c0f              0  ...      0  bias

[5 rows x 20 columns]

In [6]:
data.tail(5)

uuid  ord_in_thread  ... shares type
12994  f1b5d0e44803f48732bde854a9fdf95837219b12              2  ...      0   bs
12995  36011ceba3647e1bea78299b68b6fb705a1fc1ad              3  ...      0   bs
12996  6995d1aa9ac99926106489b14b5530e85358059a              4  ...      0   bs
12997  7de8ae90eee164eb756db6c8a3772288e11d7a94              5  ...      0   bs
12998  dabef7095b7d9dae6eb0d83c4cbb40b85efd7ae5              6  ...      0   bs

[5 rows x 20 columns]

In [7]:
y_data = data['spam_score']

In [8]:
len(y_data)

12999

In [9]:
count_0 = 0
count_1 = 0
for e in y_data:
  if(e == 1):
    count_1 = count_1 + 1
  else:
    count_0 = count_0 + 1

In [10]:
print(count_0)

12984


In [11]:
print(count_1)

15


In [12]:
# X_data is combination of text and title because content + title both can play a pivotal role in determining label

X_data = data['text'] + data['title']

In [13]:
X_data.shape

(12999,)

In [14]:
X_data[0]

'Print They should pay all the back all the money plus interest. The entire family and everyone who came in with them need to be deported asap. Why did it take two years to bust them? \nHere we go again …another group stealing from the government and taxpayers! A group of Somalis stole over four million in government benefits over just 10 months! \nWe’ve reported on numerous cases like this one where the Muslim refugees/immigrants commit fraud by scamming our system…It’s way out of control! More RelatedMuslims BUSTED: They Stole Millions In Gov’t Benefits'

# Cleaning and Tokenizing X_data and y_data

In [15]:
import matplotlib.pyplot as plt
from bs4 import BeautifulSoup
import re
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [16]:
#Data Pre-Processing(Treating Symbols and Stopwords Present in Data)

REPLACE_BY_SPACE_RE = re.compile('[/(){}\[\]\|@,;]') #These Symbols will be replaced with Space
BAD_SYMBOLS_RE = re.compile('[^0-9a-z #+_]')         #These Symbols will be Removed from Text
STOPWORDS = set(stopwords.words('english')) 

In [17]:
#Text Cleaning Functions

def string_form(value):
    return str(value)

def clean_text(text):
   
    text = BeautifulSoup(text, "lxml").text
    text = text.lower()  #LowerCase Text
    text = REPLACE_BY_SPACE_RE.sub(' ', text) #Replace Certain Symbols by Space in Text
    text = BAD_SYMBOLS_RE.sub('', text) #Delete Certain Symbols from Text
    text = ' '.join(word for word in text.split() if word not in STOPWORDS) #Remove Stopwords from Text
    return text

In [18]:
# Text Pre-processing and cleaning operations

X_data = X_data.apply(string_form)
X_data = X_data.apply(clean_text)

In [19]:
# Let us Remove all nan values

X_data_final = []
y_data_final = []

for e in range(len(X_data)):
  if(X_data[e] != 'nan'):
    X_data_final.append(X_data[e])
    y_data_final.append(y_data[e])

In [20]:
len(X_data_final)

12273

In [21]:
len(y_data_final)

12273

In [22]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(X_data_final)

In [23]:
# Let's see all the words tokenized

vocab = tokenizer.index_word
vocab

{1: 'us',
 2: 'trump',
 3: 'clinton',
 4: 'people',
 5: 'one',
 6: 'would',
 7: 'hillary',
 8: 'said',
 9: 'new',
 10: 'like',
 11: 'also',
 12: 'even',
 13: 'time',
 14: 'election',
 15: '2016',
 16: 'world',
 17: 'state',
 18: 'many',
 19: 'president',
 20: 'government',
 21: 'could',
 22: 'war',
 23: 'de',
 24: 'states',
 25: 'years',
 26: 'obama',
 27: 'american',
 28: 'media',
 29: 'get',
 30: 'first',
 31: 'campaign',
 32: 'news',
 33: 'know',
 34: 'may',
 35: 'russia',
 36: 'two',
 37: 'dont',
 38: 'donald',
 39: 'way',
 40: 'make',
 41: 'see',
 42: 'well',
 43: 'going',
 44: 'political',
 45: 'fbi',
 46: 'united',
 47: 'much',
 48: 'think',
 49: 'country',
 50: 'right',
 51: 'back',
 52: 'white',
 53: 'take',
 54: 'day',
 55: 'america',
 56: 'last',
 57: 'since',
 58: 'public',
 59: 'power',
 60: 'made',
 61: 'go',
 62: 'military',
 63: 'email',
 64: 'clintons',
 65: 'want',
 66: 'say',
 67: 'russian',
 68: 'la',
 69: 'another',
 70: 'national',
 71: 'use',
 72: 'october',
 73:

In [24]:
#We saw the tokenization of words
#Now we will get length of vocabulary then do embedding
vocab_size = len(tokenizer.word_index) + 1
vocab_size

171533

In [25]:
# We have a staggering 171533 distinct words after text cleaning

In [26]:
#We have 28711 unique words
encoded_text = tokenizer.texts_to_sequences(X_data_final)

In [27]:
#This is text data tokenized and as present in dataset, i.e as sentences
encoded_text

[[1230,
  415,
  51,
  97,
  1541,
  501,
  340,
  209,
  390,
  275,
  77,
  6432,
  16035,
  53,
  36,
  25,
  9643,
  61,
  69,
  156,
  4428,
  20,
  3317,
  156,
  30275,
  6086,
  396,
  135,
  20,
  1103,
  176,
  331,
  825,
  210,
  1384,
  798,
  10,
  5,
  574,
  1154,
  1104,
  2464,
  683,
  22313,
  82760,
  39,
  139,
  82761,
  7402,
  6086,
  397,
  3318,
  1103],
 [712,
  173,
  2946,
  1694,
  8652,
  3652,
  43644,
  6213,
  60630,
  1230,
  239,
  4809,
  1418,
  1676,
  1121,
  3677,
  434,
  178,
  414,
  8652,
  7221,
  360,
  244,
  2947,
  3885,
  823,
  3704,
  35188,
  266,
  1851,
  607,
  5207,
  21454,
  502,
  2882,
  4201,
  2946,
  1694,
  8652,
  3652,
  1080,
  6840,
  3677,
  82762,
  1843,
  712,
  173,
  2946,
  1694,
  4851,
  5779,
  114,
  785,
  290,
  296,
  26,
  2761,
  452,
  788,
  923,
  434,
  1039,
  590,
  1121,
  541,
  78,
  7580,
  2298,
  1694,
  7857,
  3652,
  1483,
  1080,
  6840,
  3677,
  73,
  3173,
  1867,
  2782,
  2477,
 

In [28]:
len(encoded_text)

12273

In [29]:
y_data_final[20]

0.19

# Finding Average Length of an article

In [30]:
# We want to keep articles which have minimum 100 words and maximum 1500 words to prevent under-fitting and over-fitting

min = 100
max = 1500
count = 0
for e in encoded_text:
  if(len(e) > min and len(e) < max):
    count = count + 1
  
count

9461

In [ ]:
# By trial and error it is observed that 9461 artciles out of 12773 fall between 100 and 1500 words
# Hence, we pad sequences to length 1500 to take care of bulk of the articles

In [31]:
#Max length of any text sequence in the dataset

max_length = 1500
X = pad_sequences(encoded_text, maxlen = max_length, padding = 'post')

In [32]:
print(X)

[[  1230    415     51 ...      0      0      0]
 [   712    173   2946 ...      0      0      0]
 [   838     17    922 ...      0      0      0]
 ...
 [  1373      7      3 ...      0      0      0]
 [171521    896    687 ...      0      0      0]
 [   896    687     15 ...      0      0      0]]


In [33]:
X.shape

(12273, 1500)

In [34]:
X[0]

array([1230,  415,   51, ...,    0,    0,    0], dtype=int32)

In [ ]:
# Now finally we have X as cleaned, tokenized and padded X_data and y_data_final as y_data

In [35]:
# Now that we have X_data and y_data we will split them

from sklearn.model_selection import train_test_split
X_train, X_test, y_train , y_test = train_test_split(X,y_data_final, test_size = 0.2)

# Using Glove Vectors


In [38]:
glove_vectors = dict()

In [39]:
file = open('/content/drive/My Drive/glove.twitter.27B.25d.txt',encoding = 'utf-8')

for line in file:
  values = line.split()
  word = values[0]
  vectors = np.asarray(values[1:])
  glove_vectors[word] = vectors
file.close()

In [40]:
#There are 1193514 words with their vectors here
len(glove_vectors.keys())

1193514

In [41]:
#Global Vector Representation of word him
glove_vectors.get('him')

array(['-0.33672', '0.66134', '0.2701', '0.92599', '-0.73521', '-0.71368',
       '0.58595', '0.051236', '-0.96658', '0.17068', '-0.64852', '1.0565',
       '-5.6538', '-0.34841', '0.21554', '-0.16274', '0.39151', '-1.0089',
       '-0.18985', '-1.0105', '0.16037', '0.59365', '0.53513', '-0.13699',
       '-0.84796'], dtype='<U8')

In [42]:
# Creating a word and correspoding vector matrix and finding out which words arent present in glove
word_vector_matrix = np.zeros((vocab_size, 25))
unavailable = 0

for word, index in tokenizer.word_index.items():
  vector = glove_vectors.get(word)
  if vector is not None:
    word_vector_matrix[index] = vector
  else:
    unavailable = unavailable + 1
    print(word)

Streaming output truncated to the last 5000 lines.
emirado
enquadrando
nomeadamente
2016em
ministrio
desmentia
relao
vtima
quartelgeneral
aliadastraduoalvaformao
negligncia
correspondncia
arquivada
financiamentos
jiadistasrede
relanamento
trafulhices
traiotecnicamente
domiclio
vestgios
limpara
dispositivoinicialmente
ambicionava
perfeitobr
forado
demitirse
erticas
separouse
deixouhuma
reproduzia
opinies
egpcio
aljazeerapor
ocasio
colgio
secretriogeral
presidncia
lobista
notcias
jordnia
publicao
anulava
assegurava
pirateadosegundo
financiou
administrao
muulmano
instncia
ignorase
sucedeu
negava
devese
pentgonoo
delegao
empregou
responsvel
emisso
recriao
mundialsabendo
antinacionalista
relaes
irmosacontece
adversrio
oprse
direo
defesandt
friandt
conspiracionista
federalescusado
organizaes
polcias
provocaram
falncia
paquistans
registado
caimo
utilizava
operaes
cartis
drogasthierry
larte
guerracome
limpegno
accodandosi
schierato
dellassemblea
negoziare
vincolante
proibire
eliminazioneil
rim

In [43]:
unavailable

96005

In [45]:
X

array([[  1230,    415,     51, ...,      0,      0,      0],
       [   712,    173,   2946, ...,      0,      0,      0],
       [   838,     17,    922, ...,      0,      0,      0],
       ...,
       [  1373,      7,      3, ...,      0,      0,      0],
       [171521,    896,    687, ...,      0,      0,      0],
       [   896,    687,     15, ...,      0,      0,      0]], dtype=int32)

In [46]:
vec_size = 25
max_length = 1500
#The glove vectors are represented in 25 dimension

In [47]:
import tensorflow as tf

In [48]:
#Let's make a keras model

model = tf.keras.Sequential()
#Now we will add embedding layer telling how many words are there and which weights to use(the glove ones)
model.add(Embedding(vocab_size, vec_size, input_length = max_length, weights = [word_vector_matrix], trainable = False))

model.add(Conv1D(128, 8 ,activation = 'relu'))
model.add(MaxPooling1D(2))
model.add(Dropout(0.3))

model.add(Conv1D(64, 4, activation = 'relu'))
model.add(MaxPooling1D(2))
model.add(Dropout(0.2))

model.add(Conv1D(32, 2, activation = 'relu'))
model.add(MaxPooling1D(2))
model.add(Dropout(0.1))

model.add(Flatten())
model.add(Dense(16, activation = 'relu' ))
model.add(Dense(8,activation = 'relu'))
model.add(Dense(1, activation = 'sigmoid'))

model.summary()


Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (None, 1500, 25)          4288325   
_________________________________________________________________
conv1d (Conv1D)              (None, 1493, 128)         25728     
_________________________________________________________________
max_pooling1d (MaxPooling1D) (None, 746, 128)          0         
_________________________________________________________________
dropout (Dropout)            (None, 746, 128)          0         
_________________________________________________________________
conv1d_1 (Conv1D)            (None, 743, 64)           32832     
_________________________________________________________________
max_pooling1d_1 (MaxPooling1 (None, 371, 64)           0         
_________________________________________________________________
dropout_1 (Dropout)          (None, 371, 64)           0

In [49]:
# Adam Optimizer was used for Experiment
adam = tf.keras.optimizers.Adadelta(learning_rate=0.001, rho=0.95)

In [50]:
model.compile(optimizer = 'adam', loss = 'binary_crossentropy', metrics = ['accuracy'])

In [51]:
X_train = np.array(X_train)
X_test = np.array(X_test)
y_train = np.array(y_train)
y_test = np.array(y_test)

In [ ]:
#Training the Model(Epochs can be tuned to get more Accuracy)
epochs = 15
batch_size = 15

history = model.fit(X_train, y_train, epochs=epochs, batch_size=batch_size,validation_data = (X_test, y_test))

In [ ]:
acc = history.history['accuracy']
val_acc = history.history['val_accuracy']
loss = history.history['loss']
val_loss = history.history['val_loss']

epochs = range(len(acc))

plt.plot(epochs, acc, 'r', label='Training accuracy')
plt.plot(epochs, val_acc, 'b', label='Validation accuracy')
plt.title('Training and validation accuracy')

plt.figure()

plt.plot(epochs, loss, 'r', label='Training Loss')
plt.plot(epochs, val_loss, 'b', label='Validation Loss')
plt.title('Training and validation loss')
plt.legend()

plt.show()

In [54]:
y_pred = model.predict(X_test)

In [55]:
y_pred.shape

(2455, 1)

In [56]:
y_pred[300]

array([0.00433428], dtype=float32)

In [57]:
from keras.models import load_model

model.save('my_model7.h5')  # creates a HDF5 file 'my_model.h5'